## The "Wild Khmer" Dataset Creation Script

In [8]:
import json
import os
import pandas as pd
from PIL import Image
from tqdm import tqdm
from datasets import Dataset, Features, Image as datasets_Image, Value

# -------------------------
# CONFIG
# -------------------------
JSON_PATH = "info.json" # Your CADT JSON file
IMAGE_FOLDER = "images/images"              # Folder with your JPGs
TRAIN_OUT = "wild_khmer_train.parquet"
TEST_OUT = "wild_khmer_test.parquet"
TEST_SPLIT = 0.1

# -------------------------
# LOAD DATA
# -------------------------
with open(JSON_PATH, 'r', encoding='utf-8') as f:
    via_data = json.load(f)
print(f"Loaded {len(via_data)} images from JSON")

# -------------------------
# DATA GENERATOR
# -------------------------
def generate_examples():
    for key, data in tqdm(via_data.items()):
        filename = data['filename']
        image_path = os.path.join(IMAGE_FOLDER, filename)

        if not os.path.exists(image_path):
            continue

        # 1. Get Image Dimensions for Normalization
        try:
            with Image.open(image_path) as img:
                width, height = img.size
                # Read raw bytes for embedding
                with open(image_path, "rb") as f:
                    img_bytes = f.read()
        except Exception as e:
            print(f"Error loading {filename}: {e}")
            continue

        # 2. Process Regions (Polygons -> Normalized Bounding Boxes)
        regions_list = []
        for region in data['regions']:
            try:
                # Extract coordinates
                xs = region['shape_attributes']['all_points_x']
                ys = region['shape_attributes']['all_points_y']
                label = region['region_attributes']['label']

                # Convert Polygon to Bounding Box (ymin, xmin, ymax, xmax)
                xmin, xmax = min(xs), max(xs)
                ymin, ymax = min(ys), max(ys)

                # Normalize to 0-1000 scale (Qwen3-VL Standard)
                n_xmin = int((xmin / width) * 1000)
                n_xmax = int((xmax / width) * 1000)
                n_ymin = int((ymin / height) * 1000)
                n_ymax = int((ymax / height) * 1000)

                # Format as a dictionary for the grounding task
                regions_list.append({
                    "bbox_2d": [n_ymin, n_xmin, n_ymax, n_xmax],
                    "label": label
                })
            except KeyError:
                continue # Skip regions without labels or points

        # 3. Create the final text label (JSON string)
        # This will be processed by your convert_to_conversation function
        grounding_json = json.dumps({"regions": regions_list}, ensure_ascii=False)

        yield {
            "image": img_bytes,
            "text": grounding_json
        }

# -------------------------
# DATASET FEATURES
# -------------------------
features = Features({
    "image": datasets_Image(),  # embedded image bytes
    "text": Value("string"),    # JSON string of boxes and text
})

# -------------------------
# CREATE & SAVE
# -------------------------
print("Processing images and labels... This may take a while.")
ds = Dataset.from_generator(generate_examples, features=features)

# Shuffle and split
ds = ds.train_test_split(test_size=TEST_SPLIT)

print("Saving Parquet files...")
ds["train"].to_parquet(TRAIN_OUT)
ds["test"].to_parquet(TEST_OUT)

print("DONE ✅")
print(f"Wild Train file: {TRAIN_OUT}")

Loaded 10000 images from JSON
Processing images and labels... This may take a while.


Generating train split: 0 examples [00:00, ? examples/s]

100%|██████████| 10000/10000 [02:28<00:00, 67.53it/s]


Loading dataset shards:   0%|          | 0/17 [00:00<?, ?it/s]

Saving Parquet files...


Creating parquet from Arrow format:   0%|          | 0/92 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/11 [00:00<?, ?ba/s]

DONE ✅
Wild Train file: wild_khmer_train.parquet


## Open The Image Dataset For Checking

In [19]:
from datasets import Dataset
ds = Dataset.from_parquet("wild_khmer_train.parquet")
sample = ds[1]["image"]
print(type(sample))
print(sample)
sample.show()


Loading dataset shards:   0%|          | 0/17 [00:00<?, ?it/s]

<class 'PIL.JpegImagePlugin.JpegImageFile'>
<PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=960x1280 at 0x219E9F9BEC0>


## DUMMY DATASET ROW

```python
{
 'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=1200x800>,
 'text': '{"regions": [{"bbox_2d": [150, 200, 300, 800], "label": "អាហារដ្ឋានមិត្តភាព"}, {"bbox_2d": [850, 400, 920, 600], "label": "012 345 678"}]}'
}
```